In [1]:
%matplotlib inline

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import scipy
import sympy as sp

from matplotlib import animation, rc
from IPython.display import HTML
rc('animation', html='jshtml')
import seaborn as sns

#Define plotting style:
sns.set() #Set style
sns.set_style('ticks',{'font.family':'serif', 'font.serif':'Times New Roman'})
sns.set_context('poster', font_scale=0.9,  rc={"lines.linewidth": 8})

#### Auxiliar function for building animation for trajectory

In [3]:
def animate2D(i,rF,vF,aF,t0,dt,rpoint,rline,vVec,aVec,title=None):
    #Get list of t points up to ith time:
    tf = t0+dt*(i+1)
    tlist = np.linspace(t0,tf,i+2,endpoint=True)
    #Get position:
    rlist = np.array([rF(t) for t in tlist])
    
    #Get position at tf:
    rf = rF(tf)
    #Get velocity at tf:
    vf = vF(tf)
    #Get acceleration at tf:
    af = aF(tf)
    
#     if title:
#         title.set_text(r't = %1.2g s' %(tf))
    
    vVec.set_offsets(rf)
    aVec.set_offsets(rf)
    vVec.set_UVC(vf[0],vf[1])
    aVec.set_UVC(af[0],af[1])
    rpoint.set_data([rlist[-1,0]],[rlist[-1,1]])
    rline.set_data(rlist[:,0],rlist[:,1])
    
    return (rline,vVec,aVec)


def setupFig(rF,vF,aF,t0,tf):
    rf = rF(tf)
    tpts = np.linspace(t0,tf,100)
    rpts = np.array([rF(t) for t in tpts])
    xmin,xmax = rpts[:,0].min(),rpts[:,0].max()
    xmin = xmin - 0.1*abs(xmin)
    xmax = xmax + 0.1*abs(xmax)
    ymin,ymax = rpts[:,1].min(),rpts[:,1].max()
    ymin = ymin - 0.1*abs(ymin)
    ymax = ymax + 0.1*abs(ymax)    
    
    v0 = vF(t0)
    a0 = aF(t0)
    r0 = rF(t0)
    
    fig = plt.figure(figsize=(8,8))
    ax1 = plt.subplot(111)
#     ax1.set_xlabel('x (m)')
#     ax1.set_ylabel('y (m)')    
    ax1.set_xlim(xmin,xmax)
    ax1.set_ylim(ymin,ymax)
    ax1.set_yticks([])
    ax1.set_xticks([])
    title = ax1.set_title("")
    
    #Make nucleus plot (fixed)
    circle = plt.Circle((0.0, 0.0), 0.05, color='cornflowerblue')
    ax1.add_patch(circle)
        
    #Make initial plots
    rpoint, = ax1.plot([r0[0]],[r0[1]],'o',markersize=14,zorder=10,color='brown') 
    rline, = ax1.plot([r0[0]],[r0[1]],'--',alpha=0.4)
    vVec = ax1.quiver(r0[0],r0[1],v0[0],v0[1],color='r',scale=21,zorder=11)
    aVec = ax1.quiver(r0[0],r0[1],a0[0],a0[1],color='g',scale=21,zorder=11)    
    plt.tight_layout()
    
    return fig,rpoint,rline,vVec,aVec,title

### Uniform Circular Movement

In [4]:
w = 2.
R = 1.

rF = lambda t: np.array([R*np.cos(w*t),R*np.sin(w*t)])
vF = lambda t: np.array([-w*R*np.sin(w*t),w*R*np.cos(w*t)])
aF = lambda t:  np.array([-w**2*R*np.cos(w*t),-w**2*R*np.sin(w*t)])
t0 = 0.
tmax = 3*np.pi/w


#Set up plot
fig,rpoint,rline,vVec,aVec,title = setupFig(rF,vF,aF,t0,tmax)
#Define time step:
dt = (tmax-t0)/200.
#Define real time step:
interval = 100

anim = animation.FuncAnimation(fig, animate2D,
                               frames=int((tmax-t0)/dt), interval=interval, 
                               blit=True, fargs=(rF,vF,aF,t0,dt,rpoint,rline,vVec,aVec,title))
plt.close()
anim


In [5]:
# Set up formatting for the movie files
Writer = animation.writers['ffmpeg']
writer = Writer(fps=15, metadata=dict(artist='AL'), bitrate=1800)
anim.save('movimentoCircular.mp4', writer=writer)